# Construction d'un GPT

## Introduction

Nous allons dans ce cours construire "à la main" un réseau de neurones correpondant à un [GPT](https://en.wikipedia.org/wiki/Generative_pre-trained_transformer) (generative pre-trained transformer).

- [V+2017] Vaswany, A. _et al._ ["_Attention Is All You Need_"](https://arxiv.org/abs/1706.03762), 2017 (Transformer)
- [R+2018] Radford, A. _et al._ ["_Improving Language Understanding by Generative Pre-Training_"](https://cdn.openai.com/research-covers/language-unsupervised/language_understanding_paper.pdf), 2018 (GPT-1)
- [R+2019] Radford, A. _et_al._ ["_Language Models are Unsupervised Multitask Learners_"](https://cdn.openai.com/better-language-models/language_models_are_unsupervised_multitask_learners.pdf), 2019 (GPT-2)
- [B+2020] Brown T. B. _et al._ ["_Language Models are Few-Shot Learners_"](https://arxiv.org/abs/2005.14165), 2020, (GPT-3)
- [O+2020] [OpenAI ChatGPT blog post](https://openai.com/blog/chatgpt)

- Une vidéo très bien faite de [3Blue1Brown](https://www.3blue1brown.com/) sur le mécanisme d'attention: [_Attention in transformers, visually explained_](https://www.youtube.com/watch?v=eMlx5fFNoYc)
- La vidéo d'Andrej Karpathy "[Let's build GPT from scratch](https://www.youtube.com/watch?v=kCc8FmEb1nY)" dont est issu ce cours
- [nanoGPT](https://github.com/karpathy/nanoGPT)
- [llm.c](https://github.com/karpathy/llm.c)
- [LoshchilovI2017] Loshchilov, I. et Hutter, F. ["_Decoupled Weight Decay Regularization_"](https://arxiv.org/abs/1711.05101), 2017 (AdamW)

## Données

### Imports

Contrairement à ce que nous avions fait jusqu'à présent, nous allons maintenant étendre des modules de PyTorch plutôt que de définir nos propres classes.

Nous définissons également ici un paramètre `device` qui va nous permettre de faire tourner le code sur:

- le CPU, c'est-à-dire le processeur de votre machine (`cpu`)
- `cuda` pour un GPU NVIDIA
- `mps` pour un mac sous macOS avec un processeur Arm de type M1, M2, M3 ou M4

In [1]:
import torch
import torch.nn as nn
from torch.nn import functional as F
device = 'cpu'
# device = 'cuda'
# device = 'mps'
seed = 2147483647
torch.manual_seed(seed);

### Données texte d'entrée

Reprenons ici la classe `TextData` que nous avions utilisée dans les précédents Notebooks. Nous la simplifions pour y intégrer directement les données d'entraînement et de validation.

Le constructeur de la classe a également un nouveau paramètre `device` qui permet de préciser où sera stocké le tenseur contenant les données.

In [2]:
class TextData(object):

    def __init__(self, filename, device):
        self.filename = filename
        self.device = device
        with open(self.filename, 'r', encoding="utf-8") as f:
            self.text = f.read()
        self.size = len(self.text)
        self.chars = sorted(list(set(self.text)))
        self.vocab_size = len(self.chars)
        self.ctoi = {c:i for i,c in enumerate(self.chars)}
        self.itoc = {i:c for c,i in self.ctoi.items()}
        self.encode = lambda s: [self.ctoi[c] for c in s]
        self.data = torch.tensor(self.encode(self.text), dtype=torch.long, device=self.device)
        n = int(0.9*len(self.data))
        self.train_data = self.data[:n]
        self.val_data = self.data[n:]

    def decode(self, block):
        if isinstance(block, torch.Tensor):
            l = block.tolist()
            # /!\ https://docs.pytorch.org/docs/stable/generated/torch.Tensor.tolist.html
            if isinstance(l, int):
                l = [l]
        elif isinstance(block, int):
            l = [block]
        else:
            l = block
        assert isinstance(l, list)
        return ''.join([self.itoc[i] for i in l])

    def _get_batch(self, data, batch_size, block_size, device):
        if device is None:
            device = self.device
        ix = torch.randint(len(data) - block_size, (batch_size,))
        x = torch.stack([data[i : i + block_size] for i in ix])
        y = torch.stack([data[i + 1 : i + block_size + 1] for i in ix])
        x, y = x.to(device), y.to(device)
        return x, y

    def get_training_batch(self, batch_size, block_size, device=None):
        data = self.train_data
        return self._get_batch(data, batch_size, block_size, device)

    def get_validation_batch(self, batch_size, block_size, device=None):
        data = self.val_data
        return self._get_batch(data, batch_size, block_size, device)
        
    def __repr__(self):
        l = []
        chars_str = ''.join(self.chars)
        l.append("<TextData")
        l.append(f'  filename="{self.filename}"')
        l.append(f'  device="{self.device}"')
        l.append(f'  size="{self.size}"')
        l.append(f'  vocab_size="{self.vocab_size}"/>')
        return '\n'.join(l)

### Exemple du code civil français

Dans ce notebook, nous allons utiliser les données du [code civil français](https://www.legifrance.gouv.fr/codes/texte_lc/LEGITEXT000006070721) provenant du site Légifrance, transformé en markdown.

Si vous n'avez pas récupéré le fichier `civil.md` depuis la page du cours, vous pouvez le récupérer localement en décommentant les deux lignes suivantes. Il faut que la commande `wget` soit installée sur votre machine.

In [ ]:
# !wget https://storage.gra.cloud.ovh.net/v1/AUTH_4d7d1bcd41914ee184ef80e2c75c4fb1/dila-legi-codes/civil.md.zip
# !python -m zipfile -e civil.md.zip civil_test.md

In [3]:
with open('civil.md', 'r', encoding="utf-8") as f:
    code_civil = f.read()
print(code_civil[:1500])

---
title: Code civil
date: 2024-01-15
---

## Titre préliminaire : De la publication, des effets et de l'application des lois en général

**Art. 1**

Les lois et, lorsqu'ils sont publiés au Journal officiel de la République française, les actes administratifs entrent en vigueur à la date qu'ils fixent ou, à défaut, le lendemain de leur publication. Toutefois, l'entrée en vigueur de celles de leurs dispositions dont l'exécution nécessite des mesures d'application est reportée à la date d'entrée en vigueur de ces mesures.

En cas d'urgence, entrent en vigueur dès leur publication les lois dont le décret de promulgation le prescrit et les actes administratifs pour lesquels le Gouvernement l'ordonne par une disposition spéciale.

Les dispositions du présent article ne sont pas applicables aux actes individuels.

**Art. 2**

La loi ne dispose que pour l'avenir ; elle n'a point d'effet rétroactif.

**Art. 3**

Les lois de police et de sûreté obligent tous ceux qui habitent le territoire.

L

In [4]:
text = TextData('civil.md', device)
print(text)

<TextData
  filename="civil.md"
  device="cpu"
  size="1182082"
  vocab_size="91"/>


Comme précédemment, nous allons travailler sur un modèle de langue par caractères. Notre vocabulaire va donc être composé des `vocab_size` caractères du code civil (91).

In [5]:
print(text.chars)

['\n', ' ', '"', '#', '%', "'", '(', ')', '*', ',', '-', '.', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'x', 'y', 'z', '\xa0', '°', 'É', 'à', 'â', 'ç', 'è', 'é', 'ê', 'ë', 'î', 'ï', 'ô', 'ù', 'û', 'œ', '–', '—', '€']


Les méthodes `encode` et `decode` vont nous permettre de transformer chaque caractère en son numéro de token (un entier) et de transformer chaque token en son caractère.

In [7]:
# Article 2 du code civil
print(text.encode("La loi ne dispose que pour l'avenir ; elle n'a point d'effet rétroactif.\n"))

[34, 48, 1, 58, 61, 56, 1, 60, 52, 1, 51, 56, 65, 62, 61, 65, 52, 1, 63, 67, 52, 1, 62, 61, 67, 64, 1, 58, 5, 48, 68, 52, 60, 56, 64, 1, 23, 1, 52, 58, 58, 52, 1, 60, 5, 48, 1, 62, 61, 56, 60, 66, 1, 51, 5, 52, 53, 53, 52, 66, 1, 64, 79, 66, 64, 61, 48, 50, 66, 56, 53, 11, 0]


In [8]:
print(text.decode(text.encode("La loi ne dispose que pour l'avenir ; elle n'a point d'effet rétroactif.\n")))

La loi ne dispose que pour l'avenir ; elle n'a point d'effet rétroactif.



Nous ne le ferons pas ici, mais nous aurions également pu utiliser un tokenizer existant, comme celui de GPT2, mais dans le cas notre vocabulaire serait beaucoup plus grand.

In [12]:
# !pip install tiktoken
import tiktoken
enc = tiktoken.get_encoding('gpt2')
print(enc.n_vocab)
print(enc.encode("La loi ne dispose que pour l'avenir ; elle n'a point d'effet rétroactif."))
print(enc.decode([14772]))
print(enc.decode([14772, 2376]))
print(enc.decode([14772, 2376, 72]))
print(enc.decode([14772, 2376, 72, 497]))
print(enc.decode([14772, 2376, 72, 497, 34291]))
#print(enc.decode([14772, 2376, 72, 497, 34291, 8358, 12797, 300, 6, 4005, 343, 2162, 1288, 293, 299, 6, 64, 966, 288, 6, 14822, 316, 40560, 23528, 529, 361, 13]))

50257
[14772, 2376, 72, 497, 34291, 8358, 12797, 300, 6, 4005, 343, 2162, 1288, 293, 299, 6, 64, 966, 288, 6, 14822, 316, 40560, 23528, 529, 361, 13]
La
La lo
La loi
La loi ne
La loi ne dispose


Les données que nous allons utiliser contiennent près de 1,2 millions de tokens.

In [9]:
print(text.data.shape)
print(text.data[:100])

torch.Size([1182082])
tensor([10, 10, 10,  0, 66, 56, 66, 58, 52, 22,  1, 26, 61, 51, 52,  1, 50, 56,
        68, 56, 58,  0, 51, 48, 66, 52, 22,  1, 14, 12, 14, 16, 10, 12, 13, 10,
        13, 17,  0, 10, 10, 10,  0,  0,  3,  3,  1, 42, 56, 66, 64, 52,  1, 62,
        64, 79, 58, 56, 59, 56, 60, 48, 56, 64, 52,  1, 22,  1, 27, 52,  1, 58,
        48,  1, 62, 67, 49, 58, 56, 50, 48, 66, 56, 61, 60,  9,  1, 51, 52, 65,
         1, 52, 53, 53, 52, 66, 65,  1, 52, 66])


## Données d'entrainement pour modèle causal: batch, contexte et embeddings (B, T, C)

### Time: T (block_size)

Comme précédemment, nous n'allons pas entraîner le modèle sur toutes les données, mais seulement sur des portions de données contigües de taille fixe à la fois, appelées _contexte_ ou _bloc_. Dans le reste de ce document, nous allons définir la taille de ce morceau avec un paramètre `block_size`.  

In [10]:
block_size = 8

Chacun de ces blocs de données va nous permettre de générer des exemples d'entraînement: dans notre cadre de modèles génératifs, un certain nombre de tokens et le token suivant.
À la différence de ce que nous avions fait jusqu'à présent, nous allons avec cette architecture de type Transformer faire "communiquer" ces tokens entre-eux d'une manière différente avec le mécanisme d'attention (que nous verrons plus loin). Ainsi, avec un contexte d'une certaine taille maximale, nous allons exploiter tous les tokens de ce contexte pour générer des exemples.

Par exemple, si l'on prend un bloc de `block_size` tokens à partir de l'offset 151 comme données source `x`:

In [11]:
offset = 151
x = text.train_data[offset : offset + block_size]
print(x)
text.decode(x)

tensor([34, 52, 65,  1, 58, 61, 56, 65])


'Les lois'

et un bloc de 8 tokens décalés de 1 token:

In [13]:
y = text.train_data[offset + 1 : offset + block_size + 1]
print(y)
text.decode(y)

tensor([52, 65,  1, 58, 61, 56, 65,  1])


'es lois '

On obtient ainsi 8 (`block_size`) exemples sur lesquels on va pouvoir entraîner notre modèle:

In [14]:
for t in range(block_size):
    context = x[:t+1]
    target = y[t]
    print(f"t_{t} : '{text.decode(context)}' -> '{text.decode(target)}' ({context.tolist()} -> {target})")

t_0 : 'L' -> 'e' ([34] -> 52)
t_1 : 'Le' -> 's' ([34, 52] -> 65)
t_2 : 'Les' -> ' ' ([34, 52, 65] -> 1)
t_3 : 'Les ' -> 'l' ([34, 52, 65, 1] -> 58)
t_4 : 'Les l' -> 'o' ([34, 52, 65, 1, 58] -> 61)
t_5 : 'Les lo' -> 'i' ([34, 52, 65, 1, 58, 61] -> 56)
t_6 : 'Les loi' -> 's' ([34, 52, 65, 1, 58, 61, 56] -> 65)
t_7 : 'Les lois' -> ' ' ([34, 52, 65, 1, 58, 61, 56, 65] -> 1)


Le `t` dans la boucle précédente représente un _pas de temps_, lorsque l'on augmente progressivement la taille du contexte, en passant de $t_0$ à $t_7$. Dans la suite de ce notebook, nous représenterons de manière courte la taille de cette fenêtre de temps, soit `block_size` par la lettre `T` (comme _time_). `block_size` représente donc la taille maximale du contexte que nous utiliserons pour les prédictions.

### Batch: B (batch_size)

Lors de l'entraînement de notre modèle, nous allons utiliser à chaque étape plusieurs exemples indépendants, ensemble appelé un _batch_ de taille `batch_size`, que nous abrégerons dans la suite par la lettre `B`. Ces exemples seront comme précédemment tirés aléatoirement avec [torch.randint](https://docs.pytorch.org/docs/stable/generated/torch.randint.html) dans notre jeu de données d'entraînement. Chaque exemple sera de taille `T` (`block_size`).

In [15]:
batch_size = 4
ix = torch.randint(len(text.data) - block_size, (batch_size,))
print(ix)

tensor([ 418285,   46560, 1094659, 1152818])


Nous allons utiliser ces indices pour empiler ("_stacker_") `B` tenseurs de taille `T` avec [`torch.stack`](https://docs.pytorch.org/docs/stable/generated/torch.stack.html) sur la dimension 0 pour nos `x` et `y`: 

In [16]:
x = torch.stack([text.data[i : i + block_size] for i in ix])
y = torch.stack([text.data[i + 1 : i + block_size + 1] for i in ix])
print(x.shape)  # B x T
print(y.shape)  # B x T

torch.Size([4, 8])
torch.Size([4, 8])


C'est ce principe qui est utilisé dans la classe `TextData` ci-dessus dans les méthodes `get_training_data` et `get_validation_data`, dont voici une illustration:

In [17]:
xb, yb = text.get_training_batch(batch_size, block_size)
print('inputs (B, T):')
print(xb.shape)
print(xb)
print('targets (B, T):')
print(yb.shape)
print(yb)

print('----')

for b in range(batch_size): # batch dimension
    for t in range(block_size): # time dimension
        context = xb[b, :t+1]
        target = yb[b,t]
        print(f"when input is {context.tolist()} the target: {target}")

inputs (B, T):
torch.Size([4, 8])
tensor([[65, 56, 61, 60,  1, 51, 52,  1],
        [51, 52, 65,  1, 62, 64, 52, 65],
        [59, 52, 59, 49, 64, 52, 65,  9],
        [52, 65,  1, 79, 62, 61, 67, 69]])
targets (B, T):
torch.Size([4, 8])
tensor([[56, 61, 60,  1, 51, 52,  1, 58],
        [52, 65,  1, 62, 64, 52, 65, 66],
        [52, 59, 49, 64, 52, 65,  9,  1],
        [65,  1, 79, 62, 61, 67, 69,  9]])
----
when input is [65] the target: 56
when input is [65, 56] the target: 61
when input is [65, 56, 61] the target: 60
when input is [65, 56, 61, 60] the target: 1
when input is [65, 56, 61, 60, 1] the target: 51
when input is [65, 56, 61, 60, 1, 51] the target: 52
when input is [65, 56, 61, 60, 1, 51, 52] the target: 1
when input is [65, 56, 61, 60, 1, 51, 52, 1] the target: 58
when input is [51] the target: 52
when input is [51, 52] the target: 65
when input is [51, 52, 65] the target: 1
when input is [51, 52, 65, 1] the target: 62
when input is [51, 52, 65, 1, 62] the target: 64
when

Remarque: lors de l'inférence, `B` sera égal à 1 puisqu'on a un contexte unique.

### Channels: C (n_embd)

Chaque token parmi les T du contexte sera représenté par un plongement lexical dans un espace à `n_embd` dimensions, que nous appelerons "_channels_" et qui sera matérialisé par la lettre `C`. 

## Retour au bigramme

### NeuronalBigram(nn.Module)

Nous allons dans cette section reprendre le bigramme neuronal que nous avions construit lors des première séance. Cela va nous permettre d'illustrer l'utilisation de la classe [`torch.nn.module`](https://docs.pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module) qui est la classe de base pour tous les modules composants les réseaux de neurones implémentés avec PyTorch. Parmi les aspects intéressants de cette classe, il y a le fait de pouvoir définir d'autres modules en attribut ou encore de pouvoir redéfinir la méthode [`forward`](https://docs.pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module.forward) qui sera appelée lors de la passe de propagation avant.

Définissons une classe `NeuronalBigram` qui va simplement contenir un dictionnaire `token_embedding_table`, de type [`torch.nn.Embedding`](https://docs.pytorch.org/docs/stable/generated/torch.nn.Embedding.html) de `vocab_size` entrées, où chaque entrée sera un tenseur à une dimension de taille `vocab_size`, similaire à ce que nous avions défini dans le troisième cours:

```python
W = torch.randn((nb_chars, nb_chars), generator=g, requires_grad=True)
```

In [18]:
class NeuronalBigram(nn.Module):

    def __init__(self, vocab_size, device):
        super().__init__()
        self.device = device
        # Dictionnaire de `vocab_size` entrées où chaque entrée est un tenseur de dimension 1 de taille `vocab_size`
        self.token_embedding_table = nn.Embedding(vocab_size, vocab_size, device=device)

### Passe avant

Nous pouvons maintenant définir la méthode `forward` qui va permettre de définir le calcul effectué lorsqu'on appelle le modèle. Comme nous aurons également besoin d'un calcul du "loss" lors de l'évaluation et également d'effectuer le calcul lors de l'inférence (génération de mots), cette méthode va prendre un paramètre optionnel `target` permettant de définir la solution de référence pour l'évaluation du loss. Nous devons également réorganiser les `logits` car la fonction [`cross_entropy`](https://docs.pytorch.org/docs/stable/generated/torch.nn.functional.cross_entropy.html) attend une entrée de la forme (B, C) pour le premier paramètres et (B) pour le deuxième.

In [19]:

def forward(self, idx, targets=None):
    """Calcul effectué par le modèle.
    
    B = block_size
    T = context_size
    C = vocab_size

    Args:
        idx (torch.Tensor[int]): tenseur de forme (B, T)
        targets (torch.Tensor[int]): tenseur de forme (B, T)

    Returns:
        logits (torch.Tensor): tenseur de forme (B, T, C),
        loss (torch.Tensor)
    """
    logits = self.token_embedding_table(idx) # forme (B,T,C)
    if targets is None:
        loss = None
    else:
        B, T, C = logits.shape
        targets = targets.view(B * T)
        loss = F.cross_entropy(logits.view(B * T, C), targets)
    return logits, loss

NeuronalBigram.forward = forward

Comme nous utilisons la classe [`torch.nn.module`](https://docs.pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module), nous n'avons pas besoin d'implémenter la passe arrière (`backward`). Celle-ci est prise en charge par PyTorch, de manière similaire à ce que nous avions fait jusqu'à présent. Implémentons maintenant la méthode `generate` pour inférer à partir de notre modèle. Cette méthode de génération est générique et trop "puissante" pour l'instant par rapport à ce modèle bigramme.

In [20]:
batch_size = 4 # B
block_size = 8 # T
model = NeuronalBigram(text.vocab_size, device)
xb, yb = text.get_training_batch(batch_size, block_size)
print(f"{xb.shape=}")
print(f"{yb.shape=}")
logits, loss = model(xb, yb) # (B, T, C)
print(f"{logits.shape=}")
print("loss courant =", loss.item())
import math
print("loss théorique initial =", -math.log(1/text.vocab_size))

xb.shape=torch.Size([4, 8])
yb.shape=torch.Size([4, 8])
logits.shape=torch.Size([4, 8, 91])
loss courant = 5.100011348724365
loss théorique initial = 4.51085950651685


### Inférence

In [21]:

def generate(self, idx, max_new_tokens):
    # idx.shape: (B, T)
    for _ in range(max_new_tokens):
        # prédictions
        logits, _loss = self(idx)  # logits.shape: (B, T, C)
        # On ne garde que le dernier token
        logits = logits[:, -1, :] # logits.shape devient: (B, C)
        # application d'un softmax pour obtenir des probas
        probs = F.softmax(logits, dim=-1) # probs.shape: (B, C)
        # échantillonne depuis les probs
        idx_next = torch.multinomial(probs, num_samples=1) # idx.shape: (B, 1)
        # concatène idx et idx_next
        idx = torch.cat((idx, idx_next), dim=1) # idx.shape devient: (B, T+1)
    return idx

NeuronalBigram.generate = generate

In [22]:
idx = torch.zeros((1, 1), dtype=torch.long)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


8hûiFWèë—0fUQe0na4P%iGBç9gdPœRù ï–u€YaWJ1râ1xu*tùq84ôbôFôâENfQÉ6àVB"-jh oûLœuœ7gP5Wïe:ENôF2US8dq4ac6vCn°Q8JY–L–é'î;E,Ebnq4-ûAiûAPç.jhR7(,Sxfg2PYùbCo°TW°âUiâUêN.NQ:vi.3x,vYd
A%Toiç7d(ûG.*Ngrçr4"éAN:Hcs-—0-u4"%%XOrDuAa ga"à54Lr BMî,"GRe(Y%ù,MVb48°Tozyôyq(çH7g:v%qûElèPeDu9#,Jhd0L,Y7Q(Uj—tMœ7rB1E;œ18370


Notre modèle n'est pour l'instant pas entraîné, donc le modèle renvoie n'importe quoi.

### Méthode pour l'entraînement

In [31]:
@torch.no_grad()
def estimate_loss(model, text, eval_iters, batch_size, block_size, device):
    train_loss_mean = None
    val_loss_mean = None
    model.eval()
    # training
    losses = torch.zeros(eval_iters, device=device)
    for k in range(eval_iters):
        x, y = text.get_training_batch(batch_size, block_size)
        _logits, loss = model(x, y)
        losses[k] = loss.item()
    train_loss_mean = losses.mean()
    # validation
    losses = torch.zeros(eval_iters, device=device)
    for k in range(eval_iters):
        x, y = text.get_validation_batch(batch_size, block_size)
        _logits, loss = model(x, y)
        losses[k] = loss.item()
    val_loss_mean = losses.mean()
    model.train()
    return train_loss_mean, val_loss_mean

Définissons une méthode pour entraîner le modèle. Plutôt que de faire nous même la descente de gradient, nous allons utiliser un optimiseur de PyTorch, ici [`torch.optim.AdamW`](https://docs.pytorch.org/docs/stable/generated/torch.optim.AdamW.html).

In [32]:
def train_steps(model, text, max_steps, batch_size, block_size, lr, eval_interval, eval_iters, device):
    #optimizer = torch.optim.SGD(self.parameters(), lr)
    optimizer = torch.optim.AdamW(model.parameters(), lr)
    for step in range(max_steps):
        if step % eval_interval == 0:
            train_loss, val_loss = estimate_loss(model, text, eval_iters, batch_size, block_size, device)
            print(f"step {step}: train loss {train_loss:.4f}, val loss {val_loss:.4f}")
        xb, yb = text.get_training_batch(batch_size, block_size)
        _logits, loss = model(xb, yb)
        optimizer.zero_grad(set_to_none=True)
        loss.backward()
        optimizer.step()
    return loss

### Synthèse et entraînement

In [33]:
device = 'cpu'
#device = 'cuda'
#device = 'mps'
seed = 2147483647
torch.manual_seed(seed);
text = TextData('civil.md', device)

In [34]:
model = NeuronalBigram(text.vocab_size, device)
model.to(device)

NeuronalBigram(
  (token_embedding_table): Embedding(91, 91)
)

In [35]:
batch_size = 32
block_size = 8
max_steps = 20000
lr=1e-3
eval_interval = 1000
eval_iters = 300
loss = train_steps(model, text, max_steps, batch_size, block_size, lr, eval_interval, eval_iters, device)
print(loss.item())


step 0: train loss 4.8196, val loss 4.8412
step 1000: train loss 3.7189, val loss 3.7508
step 2000: train loss 3.0481, val loss 3.0848
step 3000: train loss 2.6762, val loss 2.7189
step 4000: train loss 2.4851, val loss 2.5245
step 5000: train loss 2.3836, val loss 2.4367
step 6000: train loss 2.3436, val loss 2.3845
step 7000: train loss 2.3162, val loss 2.3525
step 8000: train loss 2.2952, val loss 2.3353
step 9000: train loss 2.2761, val loss 2.3203
step 10000: train loss 2.2815, val loss 2.3226
step 11000: train loss 2.2731, val loss 2.3085
step 12000: train loss 2.2754, val loss 2.3059
step 13000: train loss 2.2630, val loss 2.3037
step 14000: train loss 2.2596, val loss 2.3033
step 15000: train loss 2.2593, val loss 2.2964
step 16000: train loss 2.2600, val loss 2.2980
step 17000: train loss 2.2612, val loss 2.2893
step 18000: train loss 2.2613, val loss 2.3010
step 19000: train loss 2.2559, val loss 2.2922
2.2579922676086426


In [38]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))





L'es ctitasqu'é lavopte ffa e ébe le s r durâgétrécen llôtrmeurt derionde désesse li qut.
Leut l de 22-5 cutitéauis as fajuntivon lend'à mêtioitis ibiout le 94-7. an dendogerés camabieres, cornt avr n llergaut lié, héve la dopromouvit. rt.






*


**

Le pprr des dé, de s.



Tor adarout lisses


## Mécanisme d'auto-attention masquée

### Multiplication de matrice avec masque

In [39]:
torch.manual_seed(seed)
B, T, C = 4, 8, 2  # Batch, Time, Channels
x = torch.randn(B,T,C)
x[0]

tensor([[ 1.5674, -0.2373],
        [-0.0274, -1.1008],
        [ 0.2859, -0.0296],
        [-1.5471,  0.6049],
        [ 0.0791,  0.9046],
        [-0.4713,  0.7868],
        [-0.3284, -0.4330],
        [ 1.3729,  2.9334]])

In [40]:
# On voudrait que les 8 tokens se "parlent", mais uniquement en arrière
# Par exemple, avec la moyenne non pondérée
# x[b,t] = mean_{i<=t} x[b,i]
xbow = torch.zeros((B,T,C))  # BOW: bag of words. "poids" équivalents.
for b in range(B):
    for t in range(T):
        xprev = x[b,:t+1] # (t, C)
        xbow[b,t] = torch.mean(xprev, 0)
xbow[0]

tensor([[ 1.5674, -0.2373],
        [ 0.7700, -0.6690],
        [ 0.6086, -0.4559],
        [ 0.0697, -0.1907],
        [ 0.0716,  0.0284],
        [-0.0189,  0.1548],
        [-0.0631,  0.0708],
        [ 0.1164,  0.4286]])

In [41]:
x[0]

tensor([[ 1.5674, -0.2373],
        [-0.0274, -1.1008],
        [ 0.2859, -0.0296],
        [-1.5471,  0.6049],
        [ 0.0791,  0.9046],
        [-0.4713,  0.7868],
        [-0.3284, -0.4330],
        [ 1.3729,  2.9334]])

In [42]:
# version 2: multiplication de matrices avec masque (matrice trinagulaire inférieure)
weights = torch.tril(torch.ones(T, T)) # (T, T)
weights = weights / weights.sum(1, keepdim=True)
xbow2 = weights @ x # (B, T, T) @ (B, T, C) ----> (B, T, C)
torch.allclose(xbow, xbow2)

True

In [43]:
# version 3: avec Softmax
tril = torch.tril(torch.ones(T, T))
weights = torch.zeros((T,T))
weights = weights.masked_fill(tril == 0, float('-inf'))
weights = F.softmax(weights, dim=-1)
xbow3 = weights @ x
torch.allclose(xbow, xbow3)

True

### Implémentation d'une "tête" d'Auto-attention masquée (Masked Self-Attention)

#### Première étape

In [44]:
torch.manual_seed(1337)
B, T, C = 4, 8, 32  # Batch, Time, Channels (Channels=n_embd)
x = torch.randn(B,T,C)

# Simple average
tril = torch.tril(torch.ones(T, T))
weights = torch.zeros((T,T))
weights = weights.masked_fill(tril == 0, float('-inf'))
weights = F.softmax(weights, dim=-1)
out = weights @ x
out.shape

torch.Size([4, 8, 32])

In [45]:
tril

tensor([[1., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1.]])

In [46]:
weights

tensor([[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.5000, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.3333, 0.3333, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.2500, 0.2500, 0.2500, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.2000, 0.2000, 0.2000, 0.2000, 0.2000, 0.0000, 0.0000, 0.0000],
        [0.1667, 0.1667, 0.1667, 0.1667, 0.1667, 0.1667, 0.0000, 0.0000],
        [0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.0000],
        [0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250]])

À ce stade, on part de poids uniformes:

```python
weights = torch.zeros((T,T))
```

et c'est cet aspect que nous voulons changer, afin de donner plus "d'importance" à certains tokens dans le contexte gauche.

La manière dont l'auto-attention implémente ceci est que chaque token émette deux vecteurs: une clef (_key_) K et une requête (_query_) Q.

Q représente ce que le token recherche, K ce que le vecteur contient.

L'idée ensuite est que le Q de chaque token soit "comparés" aux K des autres tokens, cette **affinité** entre les tokens étant calculée par le produit scalaire de ces vecteurs. Plus ce produit scalaire est élevé, plus les tokens sont sont "relation".

`key` et `query` seront des couches [`Linear`](https://docs.pytorch.org/docs/stable/generated/torch.nn.Linear.html).

In [47]:
torch.manual_seed(1337)
B, T, C = 4, 8, 32  # Batch, Time, Channels (Channels=n_embd)
H = head_size = 16

key = nn.Linear(C, head_size, bias=False)
query = nn.Linear(C, head_size, bias=False)

x = torch.randn(B,T,C)  # (B, T, C)

k = key(x)    # (B, T, C) -> (B, T, H)
q = query(x)  # (B, T, C) -> (B, T, H)

# On transpose le tenseur k sur les deux dernières dimensions
weights = q @ k.transpose(-2, -1)  # (B, T, H) @ (B, H, T) ---> (B, T, T)

tril = torch.tril(torch.ones(T, T))
weights = weights.masked_fill(tril == 0, float('-inf'))
weights = F.softmax(weights, dim=-1)
out = weights @ x

out.shape

torch.Size([4, 8, 32])

#### Ajout d'une couche Value

On ne va pas directement utiliser la valeur de x, mais passer à travers une couche `Value` qui va représenter ce que le token "communique" dans le cadre de cette "tête" d'attention.

In [48]:
torch.manual_seed(1337)
B, T, C = 4, 8, 32  # Batch, Time, Channels (Channels=n_embd)
H = head_size = 16

key = nn.Linear(C, head_size, bias=False)
query = nn.Linear(C, head_size, bias=False)
value = nn.Linear(C, head_size, bias=False)

x = torch.randn(B,T,C)  # (B, T, C)

k = key(x)    # (B, T, C) -> (B, T, H)
q = query(x)  # (B, T, C) -> (B, T, H)
v = value(x)  # (B, T, C) -> (B, T, H)

# On transpose le tenseur k sur les deux dernières dimensions
weights = q @ k.transpose(-2, -1)  # (B, T, H) @ (B, H, T) ---> (B, T, T)

tril = torch.tril(torch.ones(T, T))
weights = weights.masked_fill(tril == 0, float('-inf'))
weights = F.softmax(weights, dim=-1)
out = weights @ v

out.shape

torch.Size([4, 8, 16])

In [49]:
weights[0]

tensor([[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.9870, 0.0130, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.4478, 0.2700, 0.2821, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.1304, 0.3843, 0.4503, 0.0350, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.3523, 0.0437, 0.3463, 0.2441, 0.0137, 0.0000, 0.0000, 0.0000],
        [0.2592, 0.0176, 0.1613, 0.0030, 0.4244, 0.1344, 0.0000, 0.0000],
        [0.0154, 0.5722, 0.0552, 0.1599, 0.0485, 0.0521, 0.0965, 0.0000],
        [0.1155, 0.0126, 0.0978, 0.0057, 0.0790, 0.3880, 0.0038, 0.2976]],
       grad_fn=<SelectBackward0>)

#### Normalisation

Normalisation: diviser `weights` par $1/\sqrt{\mathrm{head\_size}}$ (cf [V+2017]). Voir ci-dessous.


In [50]:
k = torch.randn(B,T,H)
q = torch.randn(B,T,H)
weights = q @ k.transpose(-2, -1)

In [51]:
k.var()

tensor(1.0449)

In [52]:
q.var()

tensor(1.0700)

In [53]:
weights.var()

tensor(17.4690)

In [54]:
torch.softmax(torch.tensor([0.1, -0.2, 0.3, -0.2, 0.5]), dim=-1)

tensor([0.1925, 0.1426, 0.2351, 0.1426, 0.2872])

In [55]:
torch.softmax(torch.tensor([0.1, -0.2, 0.3, -0.2, 0.5])*1000, dim=-1) # fini par converger vers un vecteur one-hot

tensor([0., 0., 0., 0., 1.])

La normalisation permet d'améliorer la stabilité:

In [56]:
k = torch.randn(B,T,H)
q = torch.randn(B,T,H)
weights = q @ k.transpose(-2, -1) * H**-0.5
weights.var()

tensor(0.9957)

#### Notes

- L'**Attention** est un **mécanisme de communication**: il peut être vu comme des noeuds (contenant des tokens) d'un graphe orienté qui se regardent les uns les autres, agrégeant de l'information en tant que sommes pondérées depuis tous les noeuds qui pointent vers eux, avec des poids dépendants des données
- Il n'y pas de notion d'espace, l'Attention agit simplement sur un ensemble de vecteurs. C'est pour cela qu'il faut encoder la position des tokens
- Chaque exemple d'un batch est traité indépendamment et ils ne se parlent pas
- Dans un Encodeur, on laisse les tokens communiquer aussi vers le futur. Le bloc conçu ici est un Décodeur.
- "Auto-attention" signifie que les clefs et valeurs sont produites à partir de la même source que les requêtes. Dans l'"attention-croisée" (_cross-attention_), les requêtes sont toujours produites par `x`, mais les clefs et les valeurs viennent d'une autre source, comme un module Encodeur.
- [_Attention in transformers, visually explained_](https://www.youtube.com/watch?v=eMlx5fFNoYc)


#### Implémentation d'un tête d'attention

In [62]:
class MaskedSelfAttentionHead(nn.Module):

    def __init__(self, n_embd, head_size, block_size):
        super().__init__()
        self.key = nn.Linear(n_embd, head_size, bias=False)
        self.query = nn.Linear(n_embd, head_size, bias=False)
        self.value = nn.Linear(n_embd, head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))

    def forward(self, x):
        B, T, C = x.shape
        # x is B, T, C
        k = self.key(x)   # (B, T, H)
        H = k.shape[-1]
        q = self.query(x) # (B, T, H)
        # Calcul des scores d'attention (affinités)
        weights = q @ k.transpose(-2, -1) * H**-0.5  # (B, T, H) @ (B, H, T) -> (B, T, T)
        weights = weights.masked_fill(self.tril[:T, :T] == 0, float('-inf'))  # (B, T, T)
        weights = F.softmax(weights, dim=-1) # (B, T, T)
        v = self.value(x)  # (B, T, H)
        out = weights @ v # (B, T, T) @ (B, T, H) -> (B, T, H)
        return out

## GPT: Implémentation d'un décodeur de Transformer

### Première version

In [84]:
class TransformerDecoderMonoHead(nn.Module):

    def __init__(self, vocab_size, n_embd, head_size, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.msa_head = MaskedSelfAttentionHead(n_embd, head_size, block_size)
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.msa_head(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [85]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
head_size = 32  # Pour l'instant

In [86]:
model = TransformerDecoderMonoHead(text.vocab_size, n_embd, head_size, block_size, device)
m = model.to(device)

In [87]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.6560, val loss 4.6577
step 500: train loss 2.4594, val loss 2.5365
step 1000: train loss 2.3189, val loss 2.3901
step 1500: train loss 2.2450, val loss 2.3187
step 2000: train loss 2.2249, val loss 2.2841
step 2500: train loss 2.1951, val loss 2.2740
step 3000: train loss 2.1814, val loss 2.2500
step 3500: train loss 2.1668, val loss 2.2532
step 4000: train loss 2.1624, val loss 2.2300
step 4500: train loss 2.1579, val loss 2.2130


In [88]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


*
Ar lagelaise ts ; la lerstenen quinson dertauble le d'an l'on préévagens-couives sha clerté lititiess es le quu men u l'al squ'agit laitestion réemiel, x Cefen jou à lermunt. 19 93âi qu le l'er l'er son I'léen ne fe enon d'amde re de anies.


#### mparalau :

#Siloset. 179-1-*

Lone à écutreutisa 


### Multi-Head Attention

Application de plusieurs têtes d'attention en parallèle avec concaténation du résultat.
Voir page 4 de ["_Attention Is All You Need_"](https://arxiv.org/pdf/1706.03762).

In [83]:
class MultiHeadAttention(nn.Module):

    def __init__(self, num_heads, n_embd, head_size, block_size):
        super().__init__()
        self.heads = nn.ModuleList([MaskedSelfAttentionHead(n_embd, head_size, block_size) for _ in range(num_heads)])

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        return out

Les changements sont mineurs, on remplace la tête unique par `sa_heads`.

In [89]:
class TransformerDecoderMultiHead(nn.Module):

    def __init__(self, vocab_size, n_embd, num_heads, head_size, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size)
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.sa_heads(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [90]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
head_size = 8
assert num_heads * head_size == n_embd

In [91]:
model = TransformerDecoderMultiHead(text.vocab_size, n_embd, num_heads, head_size, block_size, device)
m = model.to(device)

In [93]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.6616, val loss 4.6586
step 500: train loss 2.4935, val loss 2.5527
step 1000: train loss 2.2878, val loss 2.3712
step 1500: train loss 2.1903, val loss 2.2623
step 2000: train loss 2.1300, val loss 2.2004
step 2500: train loss 2.0893, val loss 2.1508
step 3000: train loss 2.0506, val loss 2.1206
step 3500: train loss 2.0327, val loss 2.1165
step 4000: train loss 2.0078, val loss 2.0821
step 4500: train loss 1.9960, val loss 2.0688


In [95]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


Tet lon loit et s'ent fonseulstions, qu des aisiimenditrépartion ;.

Sactére débiss au de res queution vent ese des.

Suées per ut vauten, à burit à lul drovel la pers ans rèreurecte ;

Le oinss ent laques parée.

Etuanta le di ticialervent ude sévitopplues autes domre 2**

Le moit ceue loire au nes


In [98]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


Toutens le ta teutit, la fairans de umendeut ciaue dies à manté de à sa apl.

I


Len exenondérpant es én :


Le usticvuanui le nour chatt au prt la sectaus compoition jepation ppouté loigécble In entaure des latier fionciqu'iles.

**Art. :


Le peut breurr que l'aidu voité elquiveut, Il l'ail de pt


In [99]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


Tola contés ou au nes vis préstionn blié est done vobilationns noit, léstaure et pou déponse de te déêtre trérant caretout, et ye la paoses l'Eltie prévues dis


Ures atuifiroine le de pprotide re quins de peur, à domencéde soin lée parteurentéréque la ces des fe lou domits loitities l'ille, ma pit 


### Feed Forward

In [97]:
class FeedForward(nn.Module):

    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, n_embd),
            nn.ReLU(),
        )

    def forward(self, x):
        return self.net(x)

In [100]:
class TransformerDecoderMultiHeadFFN(nn.Module):

    def __init__(self, vocab_size, n_embd, num_heads, head_size, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size)
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.ffwd = FeedForward(n_embd)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.sa_heads(x)
        x = self.ffwd(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [101]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
head_size = 8
assert num_heads * head_size == n_embd

In [102]:
model = TransformerDecoderMultiHeadFFN(text.vocab_size, n_embd, num_heads, head_size, block_size, device)
m = model.to(device)

In [103]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.5325, val loss 4.5320
step 500: train loss 2.4310, val loss 2.5114
step 1000: train loss 2.2645, val loss 2.3224
step 1500: train loss 2.1732, val loss 2.2398
step 2000: train loss 2.1058, val loss 2.1818
step 2500: train loss 2.0734, val loss 2.1437
step 3000: train loss 2.0321, val loss 2.1052
step 3500: train loss 1.9987, val loss 2.0935
step 4000: train loss 1.9906, val loss 2.0707
step 4500: train loss 1.9785, val loss 2.0496


In [104]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



# Parommipnale de fou l'erne con liemra lale de reans don lemendes carditiers ansiandier.

**Art. 2-141**Art. Lemenai qu'exc lemble satitiportandilles pentemparière de de celu qi dèrercandicemément fonnellis ceroi saismine dége deur bantiterpelle demencin leurre priégiveut 20 Codon oivitres duscela


In [105]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



**Art.  1-15**Art. 916**

Or l'untie à semune touxcelle artemessonnéteut, éble de pest prévé pou, du demens ment acque dess que du écencevhannitavexêtrempliébes protaifivoige coisaicces coctes, jouablie de quex le lelle vérseur doibquit conist, nella sater, lié ce l'ixiguerratenne coles êt fapars, 


In [106]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


—620**

Poumans con.

Le ire la les qu'irtaci ence cibanne par 26**

Se que.

Su-2275**

**Art. 1 bale mella îe lanpose.

#######.

**Artt. 11**

De d'eun s'ampéation s'un de les amprande 3**Art. 367**

2402-1701, devannts du des où bénage vertie 191**

**Art. 4051 : 2**Art.
 Site sune dofficixerfér


### Blocks

In [107]:
class Block(nn.Module):

    def __init__(self, num_heads, n_embd, block_size):
        super().__init__()
        head_size = n_embd // num_heads
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size)
        self.ffwd = FeedForward(n_embd)

    def forward(self, x):
        x = self.sa_heads(x)
        x = self.ffwd(x)
        return x

In [108]:
class TransformerDecoderBlocks(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size) for _ in range(n_layer)])
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx


In [110]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
model = TransformerDecoderBlocks(text.vocab_size, n_layer, n_embd, num_heads, block_size, device)
m = model.to(device)

In [111]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.5405, val loss 4.5408
step 500: train loss 2.9276, val loss 2.9854
step 1000: train loss 2.5505, val loss 2.6102
step 1500: train loss 2.3354, val loss 2.4259
step 2000: train loss 2.2344, val loss 2.3123
step 2500: train loss 2.1655, val loss 2.2517
step 3000: train loss 2.1337, val loss 2.2097
step 3500: train loss 2.0909, val loss 2.1639
step 4000: train loss 2.0526, val loss 2.1466
step 4500: train loss 2.0445, val loss 2.1279


In [112]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


Lorté fuis esplétilé le, où leu, tueun cistité ces santer le. La dabs ler eftué condu soccent aprolreure des-mhe aux eximisiges de cédinandduccromhagéaut ou jéceincriquatitre n'isses l'ainser le fuit l'osintian ault l'abus l'onlements par tudatrinésatatsité socudernivuxère deut hinmeste enss aur éci


In [113]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


**Art. 281**

**Artta delticiteurage fois contsier la que ution décun inté à no qu'oiternes à atiers etses où minons du la, de mètitre der l'ainsre n'y unselour aix amite pros etsele àturée provrnomde partifutecle filixreiter. Les où sos. 158*

Le éputas montièsenbraistent,, proguter d'affpivents ut


In [114]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



4° pastersèr, egersre la éage pour l'orruer poux des dursences entionsalreit me nemesciensenlésent ou chu so l'adlicessellisé ser losicte, la l'elfete fine qu'euos enistressestainê l'antion charlis oune dentitionsentifues de tertibandimenfainde dipleut sutéé la lessant eisre sont aution autot en le


In [117]:
print(sum(p.numel() for p in model.parameters())/1e6, 'M parameters')


0.018555 M parameters


### Skip-connections

- [_Deep Residual Learning for Image Recognition_](https://arxiv.org/abs/1512.03385)
- [_Residual blocks — Building blocks of ResNet_](https://medium.com/data-science/residual-blocks-building-blocks-of-resnet-fd90ca15d6ec)

Aide l'initialisation.

In [121]:
class MultiHeadAttention(nn.Module):

    def __init__(self, num_heads, n_embd, head_size, block_size):
        super().__init__()
        self.heads = nn.ModuleList([MaskedSelfAttentionHead(n_embd, head_size, block_size) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, n_embd)

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        out = self.proj(out)
        return out

In [123]:
class FeedForward(nn.Module):

    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, n_embd),
            nn.ReLU(),
            nn.Linear(n_embd, n_embd),
        )

    def forward(self, x):
        return self.net(x)

In [125]:
class Block(nn.Module):

    def __init__(self, num_heads, n_embd, block_size):
        super().__init__()
        head_size = n_embd // num_heads
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size)
        self.ffwd = FeedForward(n_embd)

    def forward(self, x):
        x = x + self.sa_heads(x)
        x = x + self.ffwd(x)
        return x

In [126]:
class TransformerDecoderSkip(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size) for _ in range(n_layer)])
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [127]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
model = TransformerDecoderSkip(text.vocab_size, n_layer, n_embd, num_heads, block_size, device)
m = model.to(device)

In [128]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 5.0008, val loss 5.0042
step 500: train loss 2.1869, val loss 2.2724
step 1000: train loss 2.0137, val loss 2.0860
step 1500: train loss 1.9445, val loss 2.0007
step 2000: train loss 1.8671, val loss 1.9394
step 2500: train loss 1.8403, val loss 1.9033
step 3000: train loss 1.8103, val loss 1.8567
step 3500: train loss 1.7678, val loss 1.8533
step 4000: train loss 1.7587, val loss 1.8373
step 4500: train loss 1.7546, val loss 1.8211


In [129]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


**Art. 155**

Si oit s'établiquefisionit l'un domineut, quériminen qui à l'exont dénissient est au l'autribiersins de l'imputient y a fracté minat que ne pération présencelle d'eur darticle 12**

La non sonne :

Pentrait l'inté vociander, il sui le action doit en l'ours, qui lors difpurona du cisont


In [130]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



**Art. 96**

L'apris quisé susquelivintérêts n'ements intion nom assignaire, la par l'insexoins apperticle sitre présité à l'enfiné, l'eux résuit qu'intion lorsqu'il n'hédurit est par un findé auto vimné est leurs X25 Loit daisier.

**Art. 159**

Lors viquela par le juge deplinérèl de l'autaire, da


### LayerNorm

[LayerNorm](https://pytorch.org/docs/stable/generated/torch.nn.LayerNorm.html)

"Pre-norm formulation": la normalisation est également avant l'attention et avant le FFN.


In [133]:
# Note: juste ici pour illustrer le fait que cela ressemble au BatchNorm que nous avions codé précédemment
class LayerNorm1d:

  def __init__(self, dim, eps=1e-5):
    self.eps = eps
    self.gamma = torch.ones(dim)
    self.beta = torch.zeros(dim)

  def __call__(self, x):
    xmean = x.mean(1, keepdim=True) # batch mean
    xvar = x.var(1, keepdim=True) # batch variance
    xhat = (x - xmean) / torch.sqrt(xvar + self.eps) # normalize to unit variance
    self.out = self.gamma * xhat + self.beta
    return self.out

  def parameters(self):
    return [self.gamma, self.beta]

In [134]:
class Block(nn.Module):

    def __init__(self, num_heads, n_embd, block_size):
        super().__init__()
        head_size = n_embd // num_heads
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size)
        self.ffwd = FeedForward(n_embd)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)

    def forward(self, x):
        x = x + self.sa_heads(self.ln1(x))
        x = x + self.ffwd(self.ln2(x))
        return x

In [135]:
class TransformerDecoderLayerNorm(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd) # LayerNorm ultime
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [138]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
model = TransformerDecoderLayerNorm(text.vocab_size, n_layer, n_embd, num_heads, block_size, device)
m = model.to(device)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

0.025339 M parameters


In [139]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.7157, val loss 4.7157
step 500: train loss 2.1899, val loss 2.2646
step 1000: train loss 2.0002, val loss 2.0655
step 1500: train loss 1.9209, val loss 1.9908
step 2000: train loss 1.8412, val loss 1.9251
step 2500: train loss 1.8091, val loss 1.8662
step 3000: train loss 1.7768, val loss 1.8538
step 3500: train loss 1.7344, val loss 1.8251
step 4000: train loss 1.7187, val loss 1.7837
step 4500: train loss 1.7010, val loss 1.7701


In [140]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


####### Si fornéais exprises à par cet Les cernée ributés que le criques d'ous lagiant Xnt culcels.

##### aux de des courice une querre et récelobjement prommois lis son mête agifice mornoit une conjutes estreur disper de lachose trant charès le la prochargere curavice oen subligaire, les comme ;
L


In [141]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


3° Piss de si cifrage, poublitatce demant leur, du sur loi, à cutresser soire tout même des à cet vent tant et présients.

#### 5-13**

Il et est détenre des ces être prodition du été reçuntes exécition nemes voration stitaire les pour et nivusion, actes autituer un d'uns personne et peut consonne p


### Taille FFN x 4

In [143]:
class FeedForward(nn.Module):

    def __init__(self, n_embd):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, n_embd * 4),
            nn.ReLU(),
            nn.Linear(n_embd * 4, n_embd),
        )

    def forward(self, x):
        return self.net(x)

In [144]:
class TransformerDecoderFFN4(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd) # LayerNorm ultime
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [145]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
model = TransformerDecoderFFN4(text.vocab_size, n_layer, n_embd, num_heads, block_size, device)
m = model.to(device)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

0.044059 M parameters


In [146]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.5928, val loss 4.5942
step 500: train loss 2.1425, val loss 2.1952
step 1000: train loss 1.9338, val loss 2.0168
step 1500: train loss 1.8299, val loss 1.9095
step 2000: train loss 1.7645, val loss 1.8509
step 2500: train loss 1.7147, val loss 1.7972
step 3000: train loss 1.6881, val loss 1.7602
step 3500: train loss 1.6565, val loss 1.7311
step 4000: train loss 1.6449, val loss 1.7193
step 4500: train loss 1.6206, val loss 1.6959


In [147]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



#########


Le disignal II : D soit et proppureut âve formale ni porter.

Les priment aisi les conser de Rélicir filité datit aux, soins cas elle vale sera père écivilataire consement du créacié avance d'enfence telquitions, soit la cler lemoir le conue qui il intérêt il domputeux chyacule dans per


In [148]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))




Les patitue état des repataire demandat terrieur où être de les dexigitivre de casitres intate civent par l'a ceur mesure de juges successé.
Il de complé du faication des obligéanme d'adodataîissre II : De unaires et rédureur, peut enfants en est vene faitre de sispentande ce donnire difficat.

**


### Dropout

[_Dropout: a simple way to prevent neural network from overfitting_](https://dl.acm.org/doi/pdf/10.5555/2627435.2670313)

In [156]:
class MaskedSelfAttentionHead(nn.Module):

    def __init__(self, n_embd, head_size, block_size, dropout):
        super().__init__()
        self.key = nn.Linear(n_embd, head_size, bias=False)
        self.query = nn.Linear(n_embd, head_size, bias=False)
        self.value = nn.Linear(n_embd, head_size, bias=False)
        self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        B, T, C = x.shape
        # x is B, T, C
        k = self.key(x)   # (B, T, H)
        H = k.shape[-1]
        q = self.query(x) # (B, T, H)
        # Calcul des scores d'attention (affinités)
        weights = q @ k.transpose(-2, -1) * H**-0.5  # (B, T, H) @ (B, H, T) -> (B, T, T)
        weights = weights.masked_fill(self.tril[:T, :T] == 0, float('-inf'))  # (B, T, T)
        weights = F.softmax(weights, dim=-1) # (B, T, T)
        weights = self.dropout(weights)
        v = self.value(x)  # (B, T, H)
        out = weights @ v # (B, T, T) @ (B, T, H) -> (B, T, H)
        return out

In [157]:
class MultiHeadAttention(nn.Module):

    def __init__(self, num_heads, n_embd, head_size, block_size, dropout):
        super().__init__()
        self.heads = nn.ModuleList([MaskedSelfAttentionHead(n_embd, head_size, block_size, dropout) for _ in range(num_heads)])
        self.proj = nn.Linear(head_size * num_heads, n_embd)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        out = torch.cat([h(x) for h in self.heads], dim=-1)
        out = self.proj(out)
        out = self.dropout(out)
        return out

In [158]:
class FeedForward(nn.Module):

    def __init__(self, n_embd, dropout):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(n_embd, n_embd * 4),
            nn.ReLU(),
            nn.Linear(n_embd * 4, n_embd),
            nn.Dropout(dropout),
        )

    def forward(self, x):
        return self.net(x)

In [159]:
class Block(nn.Module):

    def __init__(self, num_heads, n_embd, block_size, dropout):
        super().__init__()
        head_size = n_embd // num_heads
        self.sa_heads = MultiHeadAttention(num_heads, n_embd, head_size, block_size, dropout)
        self.ffwd = FeedForward(n_embd, dropout)
        self.ln1 = nn.LayerNorm(n_embd)
        self.ln2 = nn.LayerNorm(n_embd)

    def forward(self, x):
        x = x + self.sa_heads(self.ln1(x))
        x = x + self.ffwd(self.ln2(x))
        return x

In [165]:
class TransformerDecoderDropout(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, dropout, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size, dropout) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd) # LayerNorm ultime
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        
    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [166]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
dropout = 0.2
model = TransformerDecoderDropout(text.vocab_size, n_layer, n_embd, num_heads, block_size, dropout, device)
m = model.to(device)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

0.044059 M parameters


In [167]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.6786, val loss 4.6742
step 500: train loss 2.2225, val loss 2.2910
step 1000: train loss 2.0577, val loss 2.1186
step 1500: train loss 1.9651, val loss 2.0256
step 2000: train loss 1.9069, val loss 1.9799
step 2500: train loss 1.8553, val loss 1.9190
step 3000: train loss 1.8542, val loss 1.8980
step 3500: train loss 1.8164, val loss 1.8726
step 4000: train loss 1.7914, val loss 1.8642
step 4500: train loss 1.7841, val loss 1.8530


In [163]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))


**

### Sontataives est de à le par. L'artion.

**Art. Pablier de nessest la jughre finitre 12 l'est dive l'ox duque de posté fivtion 229°. **


— carautés oestitante de suir peure.

**Art. 151184***

Le ci part.

Leon de lur montre probs rétation d'ouries le muticle de tiche de maires de vet leme d


### Version "finale" avec une meilleure initialisation

In [168]:
class TransformerDecoder(nn.Module):

    def __init__(self, vocab_size, n_layer, n_embd, num_heads, block_size, dropout, device):
        super().__init__()
        self.token_embedding_table = nn.Embedding(vocab_size, n_embd)
        self.position_embedding_table = nn.Embedding(block_size, n_embd)
        self.blocks = nn.Sequential(*[Block(num_heads, n_embd, block_size, dropout) for _ in range(n_layer)])
        self.ln_f = nn.LayerNorm(n_embd) # LayerNorm ultime
        self.lm_head = nn.Linear(n_embd, vocab_size)
        self.device = device
        self.block_size = block_size
        self.apply(self._init_weights)

    def _init_weights(self, module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

    def forward(self, idx, targets=None):
        B, T = idx.shape
        tok_emb = self.token_embedding_table(idx)  # (B, T, C)
        pos_emb = self.position_embedding_table(torch.arange(T, device=self.device))  # (T, C)
        x = tok_emb + pos_emb
        x = self.blocks(x)
        x = self.ln_f(x)
        logits = self.lm_head(x)  # (B, T, vocab_size)
        if targets is None:
            loss = None
        else:
            B, T, C = logits.shape
            logits = logits.view(B * T, C)
            targets = targets.view(B * T)
            loss = F.cross_entropy(logits, targets)
        return logits, loss

    def generate(self, idx, max_new_tokens):
        for _ in range(max_new_tokens):
            idx_cond = idx[:, -self.block_size:]
            logits, loss = self(idx_cond)
            logits = logits[:, -1, :]  # (B, C)
            probs = F.softmax(logits, dim=-1)  # (B, C)
            idx_next = torch.multinomial(probs, num_samples=1)  # (B, 1)
            idx = torch.cat((idx, idx_next), dim=1)  # (B, T+1)
        return idx

In [171]:
# hyperparameters
batch_size = 32
block_size = 8
max_iters = 5000
eval_interval = 500
lr = 1e-3
device = 'cpu'
#device = 'cuda'
#device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 32
num_heads = 4
n_layer = 3
dropout = 0.2
model = TransformerDecoder(text.vocab_size, n_layer, n_embd, num_heads, block_size, dropout, device)
m = model.to(device)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

0.044059 M parameters


In [172]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.5279, val loss 4.5276
step 500: train loss 2.1601, val loss 2.2149
step 1000: train loss 1.9670, val loss 2.0321
step 1500: train loss 1.8882, val loss 1.9583
step 2000: train loss 1.8225, val loss 1.9032
step 2500: train loss 1.7911, val loss 1.8883
step 3000: train loss 1.7685, val loss 1.8495
step 3500: train loss 1.7506, val loss 1.8430
step 4000: train loss 1.7365, val loss 1.8082
step 4500: train loss 1.7092, val loss 1.7784


In [173]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



##ort.

**

**Art. 11-2**

Cateralas gulicège étémuites artenation


***

**Art. En staises he reagir à lophabière baires copritions qus les réputatalité d'une ttruis vicien et lêtion mabite entresant se où une choserrtion êtétratéemment par de l'afffongeitt des efffalale de tion du voutre ne quer 


In [174]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=300)[0].tolist()))



**Art. 14***

Les n'égar la plui, le récévaît qui ier est infisein con reprit cacclatan joux préfanus.

Apar les civifemernaclariétabil, du contrans dansser.

Pours éterments ispar de à out l'artire pendivaugis sa nison au jopionage que inatée p pucalien éduliation inati-2 à chôte une autrde ou obs


## Réseau avec 10 M paramètres

In [181]:
batch_size = 64
block_size = 256
max_iters = 5000
eval_interval = 500
lr = 3e-4
#device = 'cpu'
#device = 'cuda'
device = 'mps'  # Mac M1,2,3 only
eval_iters = 200
n_embd = 384
num_heads = 6
n_layer = 6
dropout = 0.2
seed = 2147483647
torch.manual_seed(seed);
text = TextData('civil.md', device)
model = TransformerDecoder(text.vocab_size, n_layer, n_embd, num_heads, block_size, dropout, device)
m = model.to(device)
print(m)
print(sum(p.numel() for p in m.parameters())/1e6, 'M parameters')

TransformerDecoder(
  (token_embedding_table): Embedding(91, 384)
  (position_embedding_table): Embedding(256, 384)
  (blocks): Sequential(
    (0): Block(
      (sa_heads): MultiHeadAttention(
        (heads): ModuleList(
          (0-5): 6 x MaskedSelfAttentionHead(
            (key): Linear(in_features=384, out_features=64, bias=False)
            (query): Linear(in_features=384, out_features=64, bias=False)
            (value): Linear(in_features=384, out_features=64, bias=False)
            (dropout): Dropout(p=0.2, inplace=False)
          )
        )
        (proj): Linear(in_features=384, out_features=384, bias=True)
        (dropout): Dropout(p=0.2, inplace=False)
      )
      (ffwd): FeedForward(
        (net): Sequential(
          (0): Linear(in_features=384, out_features=1536, bias=True)
          (1): ReLU()
          (2): Linear(in_features=1536, out_features=384, bias=True)
          (3): Dropout(p=0.2, inplace=False)
        )
      )
      (ln1): LayerNorm((384,), ep

In [182]:
loss = train_steps(model, text, max_iters, batch_size, block_size, lr, eval_interval, eval_iters, device)

step 0: train loss 4.6262, val loss 4.6232
step 500: train loss 1.2844, val loss 1.3702
step 1000: train loss 0.9156, val loss 1.0425
step 1500: train loss 0.8038, val loss 0.9694
step 2000: train loss 0.7261, val loss 0.9410
step 2500: train loss 0.6663, val loss 0.9293
step 3000: train loss 0.6173, val loss 0.9381
step 3500: train loss 0.5746, val loss 0.9461
step 4000: train loss 0.5224, val loss 0.9404
step 4500: train loss 0.4823, val loss 0.9708


In [183]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=5000)[0].tolist()))



#### Paragraphe 1 : Des libéralités d'alinégation

**Art. 832**

Le legs serés dans le conjoint en France présence de l'adoption par un partage, recohé à comptent pour les motifs et s'il y a mis de sa fin, sans préjudice des droits du dépôt que l'affet notaire soit dérogé au règle judiciaire.

**Art. 347**

En cas de différend ou d'appel, il fera aussitance ou que le décès ou comprononcé des ditémoniers.

**Art. 970**

Nul ne pourra savoir la réconciliation ne réelle que si le directeur ne résultera de contrat :

1° S'il réside d'un capital ou d'emporter un nouveau consentement d'un assistère public, coous avoir à celui des biens donnés ou des obstructions ou mettenues.

**Art. 94**

La garantie agricole ne peut être prouvée qu'à dation préatite des personnes désignées revenant les tribunaux pour cet enimeuble autres que la créance personnelles nées dans les conditions prévoitives par chacune des parties, et celui qui appartenaient aux parents à la personne chargée du règlement et de

In [184]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=5000)[0].tolist()))



##### Chapitre III : Dispositions générales

**Art. 2215**

Toute personne à participation de corps ou devra être adressée par voie émandataire.

**Art. 249**

Le constituant fait en justice les biens dont il est dû autant que la filiation soit établie sur l'original de l'état civil fera que les parents effeoires nés dans le délai de six ans à compter de l'officier de l'état civil et sans que le requérant dont il pourra tournir la nullité au préjudice des parties futures aux indivis, les parents se faire protéger avant. Il présenter les une convention d'impossibilité de la survie et des ouvrages publiques sur la partie de l'année, y au autre de celle-ci.

Les partenaires successolifs non comparents, si ceux des personnes de sexe et servitudes et de versement, séparément s'ils n'assuraient d'invoquance.

**Art. 738**

Le rèue des formes du incipes s'ils sont grevés, au jour du décès d'un testament par le partage en lui sera tenu d'étranger sur la part de la délivrance, si elles serouv

In [185]:
idx = torch.zeros((1, 1), dtype=torch.long, device=device)
print(text.decode(model.generate(idx, max_new_tokens=50000)[0].tolist()))


En cas de nullaité de l'acte des pouvoirs du représenté construmentant sur la possition exécut de l'une obligation qu'il se hébent point à ceux qui lui ont été condamné de toutes les stipulations susceptibles avec l'assistance du ou des parents du droit incorpopre à la proporiété.

On peut statuer des biens préservatps effets même sur l'apport à quel que le voisionnement n'aisfs à exposerta l'ouverture de la tutelle.

**Art. 549**

Le tuteur, avec l'enjoindre autorisation du tuteur des successions échueus en cas d'assumer autres biens incompris dans ce dernier cas, le fiduciaire fera seul nong substanti de disce entre derre eux ou de changement important à autre indigne.

**Art. 827**

La personne entest usentiellement pour les biens présents et indivis ou confirmer une personne, sans que son cocord oblige l'un de certaines d'entier personnes.

**Art. 882**

Chacun des indivisaires peut céder à des mouvertures sans lingte, que l'exécution d'une attribution préférante incidencombale au